##설치


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!pip install gurobipy

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.7/12.7 MB 100.8 MB/s eta 0:00:00


In [ ]:
!pip install haversine

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
!pip install pyproj

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.9/7.9 MB 92.1 MB/s eta 0:00:00


## 데이터 불러오기


In [ ]:
import numpy as np
import folium
import haversine
import pandas as pd
import pyproj

In [ ]:
#격자별 count된 demand
final = pd.read_csv('./수요량_산정/final_counted.csv')
#격자별 후보지 편의점 count
cand_count = pd.read_csv('./수요량_산정/cand_count.csv')
#격자별 기존에 설치된 BSS count
installed_count = pd.read_csv('./수요량_산정/installed_count.csv')
# BSS위치
bss_location = pd.read_csv('./수요량_산정/BSS_location.csv')

In [ ]:
#후보지가 하나라도 있는 격자만 남김
cand_count= cand_count[cand_count['NUMPOINTS']>0]

In [ ]:
#BSS가 하나라도 설치된 격자
installed_count = installed_count[installed_count['NUMPOINTS']>0]

In [ ]:
# bss 후보지가 있는 격자만 추출
index=[]
for i in range(len(final)):
    if (final['id'][i] in list(cand_count['id'])):
        index.append(i)

In [ ]:
last = final.iloc[index]

In [ ]:
last= last.reset_index(drop=True)

In [ ]:
last

id       cent_lat       cent_lon  q1_num  q2_num  q3_num  q4_num  \
0     478  183222.656677  452306.764078       0       5       4       0   
1     479  183227.979151  451306.420365       0       3       2       0   
2     480  183233.300536  450306.076649       0       0       2       0   
3     511  184223.000932  452312.087098       0       0       2       0   
4     520  184270.864029  443308.983756       0       7       1       0   
..    ...            ...            ...     ...     ...     ...     ...   
273  1535  215239.535392  451476.724642       4       1       0       0   
274  1536  215244.856957  450476.346087       1       0       1       2   
275  1537  215250.177435  449475.967525      22      12      14      14   
276  1568  216239.914486  451482.046756       0       0       0       1   
277  1569  216245.236060  450481.667113       7       5       1       8   

     weighted_num  
0             2.7  
1             1.5  
2             0.6  
3             0.6  
4             2.4  
..            ...  
273           1.5  
274           0.8  
275          15.8  
276           0.1  
277           4.7  

[278 rows x 8 columns]

In [ ]:
#bss 가 설치된 격자의 index 계산
bss_index=[]
for i in range(len(last)):
    if (last['id'][i] in list(installed_count['id'])):
        bss_index.append(i)

In [ ]:
len(bss_index)

73

In [ ]:
#위도 경도로 변환
def convert_coordinate(x, y):
    in_proj = pyproj.Proj(init='EPSG:5181')
    out_proj = pyproj.Proj(init='EPSG:4326')  # 위도와 경도를 의미하는 EPSG:4326 좌표계

    lon, lat = pyproj.transform(in_proj, out_proj, x, y)
    return lat, lon

last['lat'],last['lon']= convert_coordinate(last['cent_lat'],last['cent_lon'])

/usr/local/lib/python3.10/dist-packages/pyproj/crs/crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
/usr/local/lib/python3.10/dist-packages/pyproj/crs/crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
<ipython-input-20-aa69d6b5c9f3>:6: FutureWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lon, lat = pyproj.transform(in_proj, out_proj, x, y

## gurobi 설정

In [ ]:
from gurobipy import *
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
from haversine import haversine
import gurobipy as gp
params = {
"WLSACCESSID": '75fae455-5a37-44f7-b2d9-00896e7a5c7b',
"WLSSECRET": "4e53f1b5-4826-4999-9e8d-75ae7ccdc38e",
"LICENSEID": 2383199,
}
env = gp.Env(params=params)

# Create the model within the Gurobi environment
model = gp.Model(env=env)


Set parameter WLSAccessID
Set parameter WLSSecret
Set parameter LicenseID to value 2383199
Academic license - for non-commercial use only - registered to ghghgj@korea.ac.kr


# p-median

In [ ]:
#노드 개수 >> 1 km 격자 단위 중심점 갯수 : QGIS 상에서 70여개 정도
N=len(last)

#x.y 좌표:
np.random.seed(1)
X = last['lon'] # 중심점 경도
Y = last['lat'] # 중심점 위도

#수요량
demanda = last['weighted_num'] # 격자 단위 weighted num 이 demand
'''
#시각화:
plt.figure(figsize=(15,10))
plt.scatter(X,Y,color='blue')

for i in last.index:
    plt.annotate('$d_{%d}=%d$'%(i, demanda[i]),(X[i],Y[i]))

plt.xlabel("lon")
plt.ylabel("lat")
plt.title("nodes")
plt.show()
'''

'\n#시각화:\nplt.figure(figsize=(15,10))\nplt.scatter(X,Y,color=\'blue\')\n\nfor i in last.index:\n    plt.annotate(\'$d_{%d}=%d$\'%(i, demanda[i]),(X[i],Y[i]))\n    \nplt.xlabel("lon")\nplt.ylabel("lat")\nplt.title("nodes")\nplt.show()\n'

In [ ]:
#노드 개수 >> 1 km 격자 단위 중심점 갯수 : QGIS 상에서 70여개 정도
N=len(last)

#x.y 좌표:
np.random.seed(1)
X = last['lon'] # 중심점 경도
Y = last['lat'] # 중심점 위도

#수요량
demanda = last['weighted_num'] # 격자 단위 weighted num 이 demand
# 세트:
nodos = [i for i in range(N)]
ubicaciones = [i for i in nodos]
arcos = [(i,j) for i in nodos for j in ubicaciones]

#최대 위치 수
P= 93

#거리 행렬:
distancia = {(i,j): haversine((Y[i],X[i]),(Y[j],X[j])) for i in nodos for j in ubicaciones}
#P-median
model = Model('P-Median', env=env)

#결정변수 > 위경도 좌표 반환 > 해당 좌표와 가장 근접한 BSS 후보지 찾기
x = model.addVars(arcos,vtype = GRB.BINARY, name = 'X')
y = model.addVars(ubicaciones,vtype = GRB.BINARY, name = 'Y')

#목적함수
model.setObjective(quicksum(distancia[i,j]*x[i,j] for i,j in arcos),GRB.MINIMIZE)


#제약조건
## dist(기존 BSS, point) > dist(BSS 후보지, point)
model.addConstrs (quicksum(x[i,j] for j in ubicaciones) == 1 for i in nodos)
model.addConstr(quicksum(y[j] for j in ubicaciones) <= P)
model.addConstrs(x[i,j]-y[j] <= 0 for i in nodos for j in ubicaciones)
model.addConstrs(y[k]>=1 for k in bss_index)
model.optimize()


Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (linux64)

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Academic license - for non-commercial use only - registered to ghghgj@korea.ac.kr
Optimize a model with 77636 rows, 77562 columns and 232203 nonzeros
Model fingerprint: 0xca1c5fef
Variable types: 0 continuous, 77562 integer (77562 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 3e+01]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 9e+01]
Presolve removed 75998 rows and 75823 columns
Presolve time: 0.83s
Presolved: 1638 rows, 1739 columns, 4722 nonzeros
Variable types: 0 continuous, 1739 integer (1739 binary)
Found heuristic solution: objective 364.5710988

Root relaxation: objective 2.095951e+02, 792 iterations, 0.02 seconds (0.01 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Exp

In [ ]:
#ubicaciones Activos: 중심점으로 뽑힌애들
ubicaciones_activos = [k for k in ubicaciones if y[k].x > 0.9]

#중심점으로 뽑힌애들 중 기존 BSS 빼고 신규설치해야할 애들
sol = [x for x in ubicaciones_activos if x not in bss_index]

In [ ]:
#선정된 grid 확인
import folium

map = folium.Map(location=[37.5665, 126.9780], zoom_start=12)  # 서울을 중심으로 지도 생성

for i in range(len(last)):
    folium.Marker(location= [last['lat'][i],last['lon'][i]]).add_to(map)

for i in (sol):
    folium.Marker(location= [last['lat'][i],last['lon'][i]], icon=folium.Icon(color='red')).add_to(map)
map

#최종

In [ ]:
#최종 함수
def find(num):   #num = 추가설치할 개수
    #노드 개수 >> 1 km 격자 단위 중심점 갯수 : QGIS 상에서 70여개 정도
    N=len(last)

    #x.y 좌표:
    np.random.seed(1)
    X = last['lon'] # 중심점 경도
    Y = last['lat'] # 중심점 위도

    #수요량
    demanda = last['weighted_num'] # 격자 단위 weighted num 이 demand
    # 세트:
    nodos = [i for i in range(N)]
    ubicaciones = [i for i in nodos]
    arcos = [(i,j) for i in nodos for j in ubicaciones]

    #최대 위치 수
    P= 73 + num

    #거리 행렬:
    distancia = {(i,j): haversine((Y[i],X[i]),(Y[j],X[j])) for i in nodos for j in ubicaciones}
    #P-median
    model = Model('P-Median', env=env)

    #결정변수 > 위경도 좌표 반환 > 해당 좌표와 가장 근접한 BSS 후보지 찾기
    x = model.addVars(arcos,vtype = GRB.BINARY, name = 'X')
    y = model.addVars(ubicaciones,vtype = GRB.BINARY, name = 'Y')

    #목적함수
    model.setObjective(quicksum(distancia[i,j]*x[i,j] for i,j in arcos),GRB.MINIMIZE)


    #제약조건
    ## dist(기존 BSS, point) > dist(BSS 후보지, point)
    model.addConstrs (quicksum(x[i,j] for j in ubicaciones) == 1 for i in nodos)
    model.addConstr(quicksum(y[j] for j in ubicaciones) <= P)
    model.addConstrs(x[i,j]-y[j] <= 0 for i in nodos for j in ubicaciones)
    model.addConstrs(y[k]>=1 for k in bss_index)
    model.optimize()


    #ubicaciones Activos: 중심점으로 뽑힌애들
    ubicaciones_activos = [k for k in ubicaciones if y[k].x > 0.9]
    arcos_activos = [ k for k in arcos if x[k].x >0.9]

    #중심점으로 뽑힌애들 중 기존 BSS 빼고 신규설치해야할 애들
    sol = [x for x in ubicaciones_activos if x not in bss_index]

    dic={}
    for s in sol:
        dic[s]=[]
        for arc in arcos_activos:
            if arc[1] == s:
                dic[s].append(arc[0])


    #선정된 grid 확인
    import folium

    map = folium.Map(location=[37.5665, 126.9780], zoom_start=12)  # 서울을 중심으로 지도 생성

    for i in range(len(bss_location)):
        folium.Marker(location= [bss_location['lat'][i],bss_location['lon'][i]], icon=folium.Icon(color='black',icon = 'glyphicon-flash', prefix = 'glyphicon')).add_to(map)

    for i in (sol):
        folium.Marker(location= [last['lat'][i],last['lon'][i]], icon=folium.Icon(color='red',icon='glyphicon-ok',prefix = 'glyphicon')).add_to(map)
    display(map)

    result = last.iloc[sol]
    result['coverage']=""
    result['avg_coverage']=""
    for i in result.index:
        result['coverage'][i]= sum(dic[i])
        result['avg_coverage'][i]= np.mean(dic[i])

    return result



In [ ]:
find(10)

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (linux64)

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Academic license - for non-commercial use only - registered to ghghgj@korea.ac.kr
Optimize a model with 77636 rows, 77562 columns and 232203 nonzeros
Model fingerprint: 0xc565fe02
Variable types: 0 continuous, 77562 integer (77562 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 3e+01]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 8e+01]
Presolve removed 75998 rows and 75833 columns
Presolve time: 0.59s
Presolved: 1638 rows, 1729 columns, 4712 nonzeros
Variable types: 0 continuous, 1729 integer (1729 binary)
Found heuristic solution: objective 320.7646321

Root relaxation: objective 2.526221e+02, 1257 iterations, 0.03 seconds (0.01 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Ex

<ipython-input-29-c6b71aef4ff4>:71: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['coverage']=""
<ipython-input-29-c6b71aef4ff4>:72: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['avg_coverage']=""
<ipython-input-29-c6b71aef4ff4>:74: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['coverage'][i]= sum(dic[

id       cent_lat       cent_lon  q1_num  q2_num  q3_num  q4_num  \
1     479  183227.979151  451306.420365       0       3       2       0   
13    553  185271.209406  443314.296977       1       5       9      12   
16    579  186234.336590  450322.039189       2       2       3       4   
34    650  188261.623425  445330.935040       5       4       7       6   
37    680  189246.021993  448337.301254       8       5      15       2   
59    755  191294.548828  439344.766516       4      11       4       9   
62    777  192236.438093  450353.964377       2       0       0       1   
92    903  196205.915890  456377.395065       0       1       1       0   
94    909  196237.860871  450375.247928       0       2       1       0   
170  1160  204171.494461  463422.580323       8      45      17      30   

     weighted_num        lat         lon coverage avg_coverage  
1             1.5  37.561136  126.810171        6          1.5  
13            5.7  37.489162  126.833457       71         14.2  
16            2.5  37.552317  126.844216      175    15.909091  
34            5.4  37.507375  126.867238      327    36.333333  
37            8.6  37.534474  126.878328      445    40.454545  
59            6.6  37.453473  126.901611      297         59.4  
62            0.7  37.552675  126.912140      386    64.333333  
92            0.6  37.606970  126.957031      269    89.666667  
94            0.9  37.552891  126.957424      767       95.875  
170          24.0  37.670445  127.047283     1021   170.166667

In [ ]:
find(20)

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (linux64)

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Academic license - for non-commercial use only - registered to ghghgj@korea.ac.kr
Optimize a model with 77636 rows, 77562 columns and 232203 nonzeros
Model fingerprint: 0xca1c5fef
Variable types: 0 continuous, 77562 integer (77562 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 3e+01]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 9e+01]
Presolve removed 75998 rows and 75823 columns
Presolve time: 0.35s
Presolved: 1638 rows, 1739 columns, 4722 nonzeros
Variable types: 0 continuous, 1739 integer (1739 binary)
Found heuristic solution: objective 364.5710988

Root relaxation: objective 2.095951e+02, 792 iterations, 0.01 seconds (0.01 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Exp

<ipython-input-29-c6b71aef4ff4>:71: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['coverage']=""
<ipython-input-29-c6b71aef4ff4>:72: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['avg_coverage']=""
<ipython-input-29-c6b71aef4ff4>:74: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['coverage'][i]= sum(dic[

id       cent_lat       cent_lon  q1_num  q2_num  q3_num  q4_num  \
1     479  183227.979151  451306.420365       0       3       2       0   
4     520  184270.864029  443308.983756       0       7       1       0   
8     547  185239.310454  449316.372441       6       7       1       3   
15    578  186229.015193  451322.386171       2       0       5       0   
27    618  187266.589653  444325.271532      11      17      13      38   
29    645  188235.032736  450332.680901       0       3       0       1   
32    648  188250.990417  447331.633397      15      32      32      28   
44    713  190246.372797  448342.619943       2       4       3       0   
47    716  190262.323969  445341.565878       7      12      10       5   
59    755  191294.548828  439344.766516       4      11       4       9   
61    776  192231.116671  451354.317892       2       0       0       0   
70    811  193242.112493  449358.930649       0       0       2       1   
92    903  196205.915890  456377.395065       0       1       1       0   
94    909  196237.860871  450375.247928       0       2       1       0   
102   941  197232.897839  451380.927787       1       9       2       1   
112   976  198243.899156  449385.529683       0       1       1       1   
135  1075  201244.984221  449401.489168       4       8      34      32   
169  1159  204166.158831  464422.946820       2       6       3       2   
171  1161  204176.829004  462422.213820      16      33      19      44   
232  1307  208252.873487  448438.357231       0       2       2       3   

     weighted_num        lat         lon coverage avg_coverage  
1             1.5  37.561136  126.810171        6          1.5  
4             2.4  37.489098  126.822146       22     7.333333  
8             4.5  37.543240  126.832976       59         11.8  
15            2.1  37.561330  126.844137       73         14.6  
27           16.1  37.498301  126.856002      171         28.5  
29            1.0  37.552440  126.866857      118         29.5  
32           26.5  37.525401  126.867086      197    32.833333  
44            2.7  37.534533  126.889646      278    46.333333  
47            9.2  37.507494  126.889866      133    44.333333  
59            6.6  37.453473  126.901611      297         59.4  
61            0.6  37.561688  126.912070      176    58.666667  
70            0.7  37.543717  126.923531      210         70.0  
92            0.6  37.606970  126.957031      269    89.666667  
94            0.9  37.552891  126.957424      461         92.2  
102           3.7  37.561956  126.968681      406        101.5  
112           0.7  37.543980  126.980129      447       111.75  
135          17.0  37.544125  127.014088      679        135.8  
169           3.5  37.679458  127.047228      525        175.0  
171          24.8  37.661431  127.047338      496   165.333333  
232           1.5  37.535411  127.093376     1147        229.4

In [ ]:
LL=find(30)
LL.to_csv("/content/drive/MyDrive/캡스톤디자인/data/결과/30.csv",index=False)

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (linux64)

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Academic license - for non-commercial use only - registered to ghghgj@korea.ac.kr
Optimize a model with 77636 rows, 77562 columns and 232203 nonzeros
Model fingerprint: 0x5903b91f
Variable types: 0 continuous, 77562 integer (77562 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 3e+01]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 1e+02]
Presolve removed 75998 rows and 75818 columns
Presolve time: 0.48s
Presolved: 1638 rows, 1744 columns, 4727 nonzeros
Variable types: 0 continuous, 1744 integer (1744 binary)
Found heuristic solution: objective 325.5924179

Root relaxation: objective 1.877047e+02, 703 iterations, 0.02 seconds (0.01 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Exp

<ipython-input-29-c6b71aef4ff4>:71: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['coverage']=""
<ipython-input-29-c6b71aef4ff4>:72: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['avg_coverage']=""
<ipython-input-29-c6b71aef4ff4>:74: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['coverage'][i]= sum(dic[

In [ ]:
MM=find(21)
MM.to_csv("/content/drive/MyDrive/캡스톤디자인/data/결과/21.csv",index=False)

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (linux64)

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Academic license - for non-commercial use only - registered to ghghgj@korea.ac.kr
Optimize a model with 77636 rows, 77562 columns and 232203 nonzeros
Model fingerprint: 0x449e7647
Variable types: 0 continuous, 77562 integer (77562 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 3e+01]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 9e+01]
Presolve removed 75998 rows and 75822 columns
Presolve time: 0.42s
Presolved: 1638 rows, 1740 columns, 4723 nonzeros
Variable types: 0 continuous, 1740 integer (1740 binary)
Found heuristic solution: objective 341.4373329

Root relaxation: objective 2.071826e+02, 787 iterations, 0.02 seconds (0.01 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Exp

<ipython-input-29-c6b71aef4ff4>:71: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['coverage']=""
<ipython-input-29-c6b71aef4ff4>:72: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['avg_coverage']=""
<ipython-input-29-c6b71aef4ff4>:74: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['coverage'][i]= sum(dic[

In [ ]:
SS=find(10)
SS.to_csv("/content/drive/MyDrive/캡스톤디자인/data/결과/10.csv",index=False)

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (linux64)

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Academic license - for non-commercial use only - registered to ghghgj@korea.ac.kr
Optimize a model with 77636 rows, 77562 columns and 232203 nonzeros
Model fingerprint: 0xc565fe02
Variable types: 0 continuous, 77562 integer (77562 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 3e+01]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 8e+01]
Presolve removed 75998 rows and 75833 columns
Presolve time: 0.44s
Presolved: 1638 rows, 1729 columns, 4712 nonzeros
Variable types: 0 continuous, 1729 integer (1729 binary)
Found heuristic solution: objective 320.7646321

Root relaxation: objective 2.526221e+02, 1257 iterations, 0.02 seconds (0.01 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Ex

<ipython-input-29-c6b71aef4ff4>:71: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['coverage']=""
<ipython-input-29-c6b71aef4ff4>:72: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['avg_coverage']=""
<ipython-input-29-c6b71aef4ff4>:74: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['coverage'][i]= sum(dic[

In [ ]:
_for i in range(1,31):
    find(i)

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (linux64)

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Academic license - for non-commercial use only - registered to ghghgj@korea.ac.kr
Optimize a model with 77636 rows, 77562 columns and 232203 nonzeros
Model fingerprint: 0x15de3da9
Variable types: 0 continuous, 77562 integer (77562 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 3e+01]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 7e+01]
Presolve removed 75996 rows and 75843 columns
Presolve time: 0.82s
Presolved: 1640 rows, 1719 columns, 4702 nonzeros
Variable types: 0 continuous, 1719 integer (1719 binary)
Found heuristic solution: objective 386.2421847

Root relaxation: objective 3.606049e+02, 1730 iterations, 0.06 seconds (0.02 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Ex

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (linux64)

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Academic license - for non-commercial use only - registered to ghghgj@korea.ac.kr
Optimize a model with 77636 rows, 77562 columns and 232203 nonzeros
Model fingerprint: 0x90f989a0
Variable types: 0 continuous, 77562 integer (77562 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 3e+01]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 8e+01]
Presolve removed 75998 rows and 75841 columns
Presolve time: 1.08s
Presolved: 1638 rows, 1721 columns, 4704 nonzeros
Variable types: 0 continuous, 1721 integer (1721 binary)
Found heuristic solution: objective 368.1012376

Root relaxation: objective 3.295827e+02, 1515 iterations, 0.06 seconds (0.01 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Ex

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (linux64)

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Academic license - for non-commercial use only - registered to ghghgj@korea.ac.kr
Optimize a model with 77636 rows, 77562 columns and 232203 nonzeros
Model fingerprint: 0x5682af16
Variable types: 0 continuous, 77562 integer (77562 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 3e+01]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 8e+01]
Presolve removed 75998 rows and 75840 columns
Presolve time: 0.33s
Presolved: 1638 rows, 1722 columns, 4705 nonzeros
Variable types: 0 continuous, 1722 integer (1722 binary)
Found heuristic solution: objective 361.8550358

Root relaxation: objective 3.151376e+02, 1470 iterations, 0.03 seconds (0.01 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Ex

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (linux64)

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Academic license - for non-commercial use only - registered to ghghgj@korea.ac.kr
Optimize a model with 77636 rows, 77562 columns and 232203 nonzeros
Model fingerprint: 0xdb983086
Variable types: 0 continuous, 77562 integer (77562 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 3e+01]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 8e+01]
Presolve removed 75998 rows and 75839 columns
Presolve time: 0.45s
Presolved: 1638 rows, 1723 columns, 4706 nonzeros
Variable types: 0 continuous, 1723 integer (1723 binary)
Found heuristic solution: objective 351.6716744

Root relaxation: objective 3.025655e+02, 1440 iterations, 0.03 seconds (0.01 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Ex

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (linux64)

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Academic license - for non-commercial use only - registered to ghghgj@korea.ac.kr
Optimize a model with 77636 rows, 77562 columns and 232203 nonzeros
Model fingerprint: 0x05fadd88
Variable types: 0 continuous, 77562 integer (77562 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 3e+01]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 8e+01]
Presolve removed 75998 rows and 75838 columns
Presolve time: 0.35s
Presolved: 1638 rows, 1724 columns, 4707 nonzeros
Variable types: 0 continuous, 1724 integer (1724 binary)
Found heuristic solution: objective 347.8012264

Root relaxation: objective 2.909982e+02, 1345 iterations, 0.03 seconds (0.01 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Ex

...

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (linux64)

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Academic license - for non-commercial use only - registered to ghghgj@korea.ac.kr
Optimize a model with 77636 rows, 77562 columns and 232203 nonzeros
Model fingerprint: 0x485c19fc
Variable types: 0 continuous, 77562 integer (77562 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 3e+01]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 9e+01]
Presolve removed 75998 rows and 75827 columns
Presolve time: 0.43s
Presolved: 1638 rows, 1735 columns, 4718 nonzeros
Variable types: 0 continuous, 1735 integer (1735 binary)
Found heuristic solution: objective 298.8622152

Root relaxation: objective 2.219125e+02, 930 iterations, 0.02 seconds (0.01 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Exp

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (linux64)

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Academic license - for non-commercial use only - registered to ghghgj@korea.ac.kr
Optimize a model with 77636 rows, 77562 columns and 232203 nonzeros
Model fingerprint: 0x8aa75112
Variable types: 0 continuous, 77562 integer (77562 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 3e+01]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 9e+01]
Presolve removed 75998 rows and 75826 columns
Presolve time: 0.43s
Presolved: 1638 rows, 1736 columns, 4719 nonzeros
Variable types: 0 continuous, 1736 integer (1736 binary)
Found heuristic solution: objective 334.5568013

Root relaxation: objective 2.185019e+02, 905 iterations, 0.02 seconds (0.01 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Exp

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (linux64)

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Academic license - for non-commercial use only - registered to ghghgj@korea.ac.kr
Optimize a model with 77636 rows, 77562 columns and 232203 nonzeros
Model fingerprint: 0x6fb59429
Variable types: 0 continuous, 77562 integer (77562 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 3e+01]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 9e+01]
Presolve removed 75998 rows and 75825 columns
Presolve time: 0.44s
Presolved: 1638 rows, 1737 columns, 4720 nonzeros
Variable types: 0 continuous, 1737 integer (1737 binary)
Found heuristic solution: objective 333.5587980

Root relaxation: objective 2.152610e+02, 859 iterations, 0.02 seconds (0.01 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Exp

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (linux64)

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Academic license - for non-commercial use only - registered to ghghgj@korea.ac.kr
Optimize a model with 77636 rows, 77562 columns and 232203 nonzeros
Model fingerprint: 0xcf991210
Variable types: 0 continuous, 77562 integer (77562 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 3e+01]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 9e+01]
Presolve removed 75998 rows and 75824 columns
Presolve time: 0.44s
Presolved: 1638 rows, 1738 columns, 4721 nonzeros
Variable types: 0 continuous, 1738 integer (1738 binary)
Found heuristic solution: objective 332.3423537

Root relaxation: objective 2.124238e+02, 840 iterations, 0.02 seconds (0.01 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Exp

KeyboardInterrupt: ignored

In [ ]:
find(20)

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (linux64)

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Academic license - for non-commercial use only - registered to ghghgj@korea.ac.kr
Optimize a model with 77636 rows, 77562 columns and 232203 nonzeros
Model fingerprint: 0xca1c5fef
Variable types: 0 continuous, 77562 integer (77562 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 3e+01]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 9e+01]
Presolve removed 75998 rows and 75823 columns
Presolve time: 0.28s
Presolved: 1638 rows, 1739 columns, 4722 nonzeros
Variable types: 0 continuous, 1739 integer (1739 binary)
Found heuristic solution: objective 364.5710988

Root relaxation: objective 2.095951e+02, 792 iterations, 0.01 seconds (0.01 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Exp

id       cent_lat       cent_lon  q1_num  q2_num  q3_num  q4_num  \
1     479  183227.979151  451306.420365       0       3       2       0   
4     520  184270.864029  443308.983756       0       7       1       0   
8     547  185239.310454  449316.372441       6       7       1       3   
15    578  186229.015193  451322.386171       2       0       5       0   
27    618  187266.589653  444325.271532      11      17      13      38   
29    645  188235.032736  450332.680901       0       3       0       1   
32    648  188250.990417  447331.633397      15      32      32      28   
44    713  190246.372797  448342.619943       2       4       3       0   
47    716  190262.323969  445341.565878       7      12      10       5   
59    755  191294.548828  439344.766516       4      11       4       9   
61    776  192231.116671  451354.317892       2       0       0       0   
70    811  193242.112493  449358.930649       0       0       2       1   
92    903  196205.915890  456377.395065       0       1       1       0   
94    909  196237.860871  450375.247928       0       2       1       0   
102   941  197232.897839  451380.927787       1       9       2       1   
112   976  198243.899156  449385.529683       0       1       1       1   
135  1075  201244.984221  449401.489168       4       8      34      32   
169  1159  204166.158831  464422.946820       2       6       3       2   
171  1161  204176.829004  462422.213820      16      33      19      44   
232  1307  208252.873487  448438.357231       0       2       2       3   

     weighted_num        lat         lon  
1             1.5  37.561136  126.810171  
4             2.4  37.489098  126.822146  
8             4.5  37.543240  126.832976  
15            2.1  37.561330  126.844137  
27           16.1  37.498301  126.856002  
29            1.0  37.552440  126.866857  
32           26.5  37.525401  126.867086  
44            2.7  37.534533  126.889646  
47            9.2  37.507494  126.889866  
59            6.6  37.453473  126.901611  
61            0.6  37.561688  126.912070  
70            0.7  37.543717  126.923531  
92            0.6  37.606970  126.957031  
94            0.9  37.552891  126.957424  
102           3.7  37.561956  126.968681  
112           0.7  37.543980  126.980129  
135          17.0  37.544125  127.014088  
169           3.5  37.679458  127.047228  
171          24.8  37.661431  127.047338  
232           1.5  37.535411  127.093376

In [ ]:
find(10)

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (linux64)

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Academic license - for non-commercial use only - registered to ghghgj@korea.ac.kr
Optimize a model with 77636 rows, 77562 columns and 232203 nonzeros
Model fingerprint: 0xc565fe02
Variable types: 0 continuous, 77562 integer (77562 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 3e+01]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 8e+01]
Presolve removed 75998 rows and 75833 columns
Presolve time: 0.92s
Presolved: 1638 rows, 1729 columns, 4712 nonzeros
Variable types: 0 continuous, 1729 integer (1729 binary)
Found heuristic solution: objective 320.7646321

Root relaxation: objective 2.526221e+02, 1257 iterations, 0.04 seconds (0.01 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Ex

id       cent_lat       cent_lon  q1_num  q2_num  q3_num  q4_num  \
1     479  183227.979151  451306.420365       0       3       2       0   
13    553  185271.209406  443314.296977       1       5       9      12   
16    579  186234.336590  450322.039189       2       2       3       4   
34    650  188261.623425  445330.935040       5       4       7       6   
37    680  189246.021993  448337.301254       8       5      15       2   
59    755  191294.548828  439344.766516       4      11       4       9   
62    777  192236.438093  450353.964377       2       0       0       1   
92    903  196205.915890  456377.395065       0       1       1       0   
94    909  196237.860871  450375.247928       0       2       1       0   
170  1160  204171.494461  463422.580323       8      45      17      30   

     weighted_num        lat         lon  
1             1.5  37.561136  126.810171  
13            5.7  37.489162  126.833457  
16            2.5  37.552317  126.844216  
34            5.4  37.507375  126.867238  
37            8.6  37.534474  126.878328  
59            6.6  37.453473  126.901611  
62            0.7  37.552675  126.912140  
92            0.6  37.606970  126.957031  
94            0.9  37.552891  126.957424  
170          24.0  37.670445  127.047283

In [ ]:
m_id

id       cent_lat       cent_lon  q1_num  q2_num  q3_num  q4_num  \
1     479  183227.979151  451306.420365       0       3       2       0   
4     520  184270.864029  443308.983756       0       7       1       0   
8     547  185239.310454  449316.372441       6       7       1       3   
15    578  186229.015193  451322.386171       2       0       5       0   
27    618  187266.589653  444325.271532      11      17      13      38   
29    645  188235.032736  450332.680901       0       3       0       1   
32    648  188250.990417  447331.633397      15      32      32      28   
44    713  190246.372797  448342.619943       2       4       3       0   
47    716  190262.323969  445341.565878       7      12      10       5   
59    755  191294.548828  439344.766516       4      11       4       9   
61    776  192231.116671  451354.317892       2       0       0       0   
70    811  193242.112493  449358.930649       0       0       2       1   
92    903  196205.915890  456377.395065       0       1       1       0   
94    909  196237.860871  450375.247928       0       2       1       0   
102   941  197232.897839  451380.927787       1       9       2       1   
112   976  198243.899156  449385.529683       0       1       1       1   
135  1075  201244.984221  449401.489168       4       8      34      32   
169  1159  204166.158831  464422.946820       2       6       3       2   
171  1161  204176.829004  462422.213820      16      33      19      44   
232  1307  208252.873487  448438.357231       0       2       2       3   
274  1536  215244.856957  450476.346087       1       0       1       2   

     weighted_num        lat         lon  
1             1.5  37.561136  126.810171  
4             2.4  37.489098  126.822146  
8             4.5  37.543240  126.832976  
15            2.1  37.561330  126.844137  
27           16.1  37.498301  126.856002  
29            1.0  37.552440  126.866857  
32           26.5  37.525401  126.867086  
44            2.7  37.534533  126.889646  
47            9.2  37.507494  126.889866  
59            6.6  37.453473  126.901611  
61            0.6  37.561688  126.912070  
70            0.7  37.543717  126.923531  
92            0.6  37.606970  126.957031  
94            0.9  37.552891  126.957424  
102           3.7  37.561956  126.968681  
112           0.7  37.543980  126.980129  
135          17.0  37.544125  127.014088  
169           3.5  37.679458  127.047228  
171          24.8  37.661431  127.047338  
232           1.5  37.535411  127.093376  
274           0.8  37.553684  127.172527

In [ ]:
s_id= find(10)
m_id= find(21)
l_id= find(30)

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (linux64)

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Academic license - for non-commercial use only - registered to ghghgj@korea.ac.kr
Optimize a model with 77636 rows, 77562 columns and 232203 nonzeros
Model fingerprint: 0xc565fe02
Variable types: 0 continuous, 77562 integer (77562 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 3e+01]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 8e+01]
Presolve removed 75998 rows and 75833 columns
Presolve time: 0.31s
Presolved: 1638 rows, 1729 columns, 4712 nonzeros
Variable types: 0 continuous, 1729 integer (1729 binary)
Found heuristic solution: objective 320.7646321

Root relaxation: objective 2.526221e+02, 1257 iterations, 0.09 seconds (0.01 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Ex

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (linux64)

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Academic license - for non-commercial use only - registered to ghghgj@korea.ac.kr
Optimize a model with 77636 rows, 77562 columns and 232203 nonzeros
Model fingerprint: 0x449e7647
Variable types: 0 continuous, 77562 integer (77562 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 3e+01]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 9e+01]
Presolve removed 75998 rows and 75822 columns
Presolve time: 0.47s
Presolved: 1638 rows, 1740 columns, 4723 nonzeros
Variable types: 0 continuous, 1740 integer (1740 binary)
Found heuristic solution: objective 341.4373329

Root relaxation: objective 2.071826e+02, 787 iterations, 0.02 seconds (0.01 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Exp

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (linux64)

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Academic license - for non-commercial use only - registered to ghghgj@korea.ac.kr
Optimize a model with 77636 rows, 77562 columns and 232203 nonzeros
Model fingerprint: 0x5903b91f
Variable types: 0 continuous, 77562 integer (77562 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 3e+01]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 1e+02]
Presolve removed 75998 rows and 75818 columns
Presolve time: 0.23s
Presolved: 1638 rows, 1744 columns, 4727 nonzeros
Variable types: 0 continuous, 1744 integer (1744 binary)
Found heuristic solution: objective 325.5924179

Root relaxation: objective 1.877047e+02, 703 iterations, 0.02 seconds (0.01 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Exp

In [ ]:
#s_id.to_csv('/content/drive/MyDrive/캡스톤디자인/대중소/10_id.csv', index=False)
#m_id.to_csv('/content/drive/MyDrive/캡스톤디자인/대중소/20_id.csv', index=False)
#l_id.to_csv('/content/drive/MyDrive/캡스톤디자인/대중소/30_id.csv', index=False)

In [ ]:
#결과보여주는 함수
def vis(num):   #num = 추가설치할 개수
    #노드 개수 >> 1 km 격자 단위 중심점 갯수 : QGIS 상에서 70여개 정도
    N=len(last)

    #x.y 좌표:
    np.random.seed(1)
    X = last['lon'] # 중심점 경도
    Y = last['lat'] # 중심점 위도

    #수요량
    demanda = last['weighted_num'] # 격자 단위 weighted num 이 demand
    # 세트:
    nodos = [i for i in range(N)]
    ubicaciones = [i for i in nodos]
    arcos = [(i,j) for i in nodos for j in ubicaciones]

    #최대 위치 수
    P= 73 + num

    #거리 행렬:
    distancia = {(i,j): haversine((Y[i],X[i]),(Y[j],X[j])) for i in nodos for j in ubicaciones}
    #P-median
    model = Model('P-Median', env=env)

    #결정변수 > 위경도 좌표 반환 > 해당 좌표와 가장 근접한 BSS 후보지 찾기
    x = model.addVars(arcos,vtype = GRB.BINARY, name = 'X')
    y = model.addVars(ubicaciones,vtype = GRB.BINARY, name = 'Y')

    #목적함수
    model.setObjective(quicksum(distancia[i,j]*x[i,j] for i,j in arcos),GRB.MINIMIZE)


    #제약조건
    ## dist(기존 BSS, point) > dist(BSS 후보지, point)
    model.addConstrs (quicksum(x[i,j] for j in ubicaciones) == 1 for i in nodos)
    model.addConstr(quicksum(y[j] for j in ubicaciones) <= P)
    model.addConstrs(x[i,j]-y[j] <= 0 for i in nodos for j in ubicaciones)
    model.addConstrs(y[k]>=1 for k in bss_index)
    model.optimize()


    #ubicaciones Activos: 중심점으로 뽑힌애들
    ubicaciones_activos = [k for k in ubicaciones if y[k].x > 0.9]

    #중심점으로 뽑힌애들 중 기존 BSS 빼고 신규설치해야할 애들
    sol = [x for x in ubicaciones_activos if x not in bss_index]
    '''
    #선정된 grid 확인
    import folium

    map = folium.Map(location=[37.5665, 126.9780], zoom_start=12)  # 서울을 중심으로 지도 생성

    for i in range(len(bss_location)):
        folium.Marker(location= [bss_location['lat'][i],bss_location['lon'][i]], icon=folium.Icon(color='black',icon = 'glyphicon-flash', prefix = 'glyphicon')).add_to(map)

    for i in (sol):
        folium.Marker(location= [last['lat'][i],last['lon'][i]], icon=folium.Icon(color='red',icon='glyphicon-ok',prefix = 'glyphicon')).add_to(map)
    display(map)
    '''

    return sol



In [ ]:
s1= vis(10)
s2= vis(21)
s3= vis(30)

s2_new= [x for x in s2 if x not in s1]
s3_new= [x for x in s3 if x not in s2]

import folium

map = folium.Map(location=[37.5665, 126.9780], zoom_start=12)  # 서울을 중심으로 지도 생성

for i in range(len(bss_location)):
    folium.Marker(location= [bss_location['lat'][i],bss_location['lon'][i]], icon=folium.Icon(color='black',icon = 'glyphicon-flash', prefix = 'glyphicon')).add_to(map)

for i in (s1):
    folium.Marker(location= [last['lat'][i],last['lon'][i]], icon=folium.Icon(color='red',icon='glyphicon-ok',prefix = 'glyphicon')).add_to(map)


for i in (s2_new):
    folium.Marker(location= [last['lat'][i],last['lon'][i]], icon=folium.Icon(color='blue',icon='glyphicon-ok',prefix = 'glyphicon')).add_to(map)

'''
for i in (s3_new):
    folium.Marker(location= [last['lat'][i],last['lon'][i]], icon=folium.Icon(color='blue',icon='glyphicon-ok',prefix = 'glyphicon')).add_to(map)
'''
display(map)





Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (linux64)

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Academic license - for non-commercial use only - registered to ghghgj@korea.ac.kr
Optimize a model with 77636 rows, 77562 columns and 232203 nonzeros
Model fingerprint: 0xc565fe02
Variable types: 0 continuous, 77562 integer (77562 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 3e+01]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 8e+01]
Presolve removed 75998 rows and 75833 columns
Presolve time: 0.84s
Presolved: 1638 rows, 1729 columns, 4712 nonzeros
Variable types: 0 continuous, 1729 integer (1729 binary)
Found heuristic solution: objective 320.7646321

Root relaxation: objective 2.526221e+02, 1257 iterations, 0.04 seconds (0.01 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Ex

In [ ]:
map = folium.Map(location=[37.5665, 126.9780], zoom_start=12)  # 서울을 중심으로 지도 생성

for i in range(len(bss_location)):
    folium.Marker(location= [bss_location['lat'][i],bss_location['lon'][i]], icon=folium.Icon(color='black',icon = 'glyphicon-flash', prefix = 'glyphicon')).add_to(map)

for i in (s1):
    folium.Marker(location= [last['lat'][i],last['lon'][i]], icon=folium.Icon(color='red',icon='glyphicon-ok',prefix = 'glyphicon')).add_to(map)


display(map)

In [ ]:
map = folium.Map(location=[37.5665, 126.9780], zoom_start=12)  # 서울을 중심으로 지도 생성

for i in range(len(bss_location)):
    folium.Marker(location= [bss_location['lat'][i],bss_location['lon'][i]], icon=folium.Icon(color='black',icon = 'glyphicon-flash', prefix = 'glyphicon')).add_to(map)

for i in (s1):
    folium.Marker(location= [last['lat'][i],last['lon'][i]], icon=folium.Icon(color='red',icon='glyphicon-ok',prefix = 'glyphicon')).add_to(map)


for i in (s2_new):
    folium.Marker(location= [last['lat'][i],last['lon'][i]], icon=folium.Icon(color='blue',icon='glyphicon-ok',prefix = 'glyphicon')).add_to(map)


for i in (s3_new):
    folium.Marker(location= [last['lat'][i],last['lon'][i]], icon=folium.Icon(color='orange',icon='glyphicon-ok',prefix = 'glyphicon')).add_to(map)

display(map)



## 최종 후보지

In [ ]:
# 교통량 커버 데이터

cover = pd.read_csv("./전처리/후보지_커버_수요량/cand_coverage_weighted_count.csv")
cover.head()

grid_id            lat            lon  weighted_count
0     1047  444438.799903  199860.799573          1228.3
1        0  184009.999829  188126.396529             0.0
2      917  442356.000426  196544.803630          1077.7
3     1105  452675.799845  202215.698732             8.7
4     1469  451015.499984  213355.001385            10.4

In [ ]:
cover['lat_'],cover['lon_']= convert_coordinate(cover['lon'],cover['lat'])

/usr/local/lib/python3.10/dist-packages/pyproj/crs/crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
/usr/local/lib/python3.10/dist-packages/pyproj/crs/crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
<ipython-input-18-aa69d6b5c9f3>:6: FutureWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lon, lat = pyproj.transform(in_proj, out_proj, x, y

In [ ]:
cover

grid_id            lat            lon  weighted_count       lat_  \
0       1047  444438.799903  199860.799573          1228.3  37.499411   
1          0  184009.999829  188126.396529             0.0  35.152398   
2        917  442356.000426  196544.803630          1077.7  37.480639   
3       1105  452675.799845  202215.698732             8.7  37.573624   
4       1469  451015.499984  213355.001385            10.4  37.558571   
..       ...            ...            ...             ...        ...   
891     1072  452412.799976  201510.796083            10.1  37.571256   
892     1112  445529.200277  202313.198867          9895.9  37.509233   
893      937  455034.400193  196807.998718             0.0  37.594872   
894     1037  454036.000298  199735.601896             1.5  37.585882   
895     1072  452346.000036  201123.004256            12.0  37.570655   

           lon_  
0    126.998426  
1    126.869691  
2    126.960935  
3    127.025082  
4    127.151149  
..          ...  
891  127.017102  
892  127.026163  
893  126.963856  
894  126.997006  
895  127.012712  

[896 rows x 6 columns]

In [ ]:
len(s_id), len(m_id), len(l_id)

(10, 21, 30)

In [ ]:
def find_cand(id) :
    install_list = []
    no_cand = []
    id_list = list(id['id'].values)
    for i in id_list :
        cand_list = cover[cover['grid_id'] == i].sort_values('weighted_count', ascending = False)
        if len(cand_list) >= 1 :
            install_list.append([cand_list['lat'].iloc[0], cand_list['lon'].iloc[0]])
        else :
            no_cand.append(i)

    map = folium.Map(location=[37.5665, 126.9780], zoom_start=12)

    for i in range(len(install_list)):
        folium.Marker(location= [install_list[i][0],install_list[i][1]], icon=folium.Icon(color='black',icon = 'glyphicon-flash', prefix = 'glyphicon')).add_to(map)
    display(map)

    return no_cand
    #for i in (sol):
        #folium.Marker(location= [last['lat'][i],last['lon'][i]], icon=folium.Icon(color='red',icon='glyphicon-ok',prefix = 'glyphicon')).add_to(map)
    #display(map)


In [ ]:
install_list_lat = []
install_list_lon = []
no_cand = []
id_list = list(m_id['id'].values)
for i in id_list :
    cand_list = cover[cover['grid_id'] == i].sort_values('weighted_count', ascending = False)
    if len(cand_list) >= 1 :
        install_list_lat.append(cand_list['lat'].iloc[0])
        install_list_lon.append(cand_list['lon'].iloc[0])
    else :
        no_cand.append(i)

dd = pd.DataFrame({'lat' : install_list_lat, 'lon' : install_list_lon})